In [35]:
from pyspark.sql import SparkSession

# Create SparkSession 
spark = SparkSession.builder \
      .master("local[1]") \
      .appName("Data_join") \
      .getOrCreate() 



Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


22/12/20 16:51:02 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [36]:
spark

In [37]:
# Einlesen von Dateien in Spark, Datei Typ einfach Anpassen
basics = spark.read.option("header", True).csv("Spark/title_basics.tsv", sep='\t', encoding='utf8')
basics.show()

+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+--------------------+
|   tconst|titleType|        primaryTitle|       originalTitle|isAdult|startYear|endYear|runtimeMinutes|              genres|
+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+--------------------+
|tt0000001|    short|          Carmencita|          Carmencita|      0|     1894|     \N|             1|   Documentary,Short|
|tt0000002|    short|Le clown et ses c...|Le clown et ses c...|      0|     1892|     \N|             5|     Animation,Short|
|tt0000003|    short|      Pauvre Pierrot|      Pauvre Pierrot|      0|     1892|     \N|             4|Animation,Comedy,...|
|tt0000004|    short|         Un bon bock|         Un bon bock|      0|     1892|     \N|            12|     Animation,Short|
|tt0000005|    short|    Blacksmith Scene|    Blacksmith Scene|      0|     1893|     \N|             1|        Comedy

In [38]:
import time
time1=time.time()
ratings = spark.read.option("header", True).csv("Spark/title_ratings.tsv", sep='\t', encoding='utf8')
ratings.show()
time2=time.time()
print(time2-time1)

+---------+-------------+--------+
|   tconst|averageRating|numVotes|
+---------+-------------+--------+
|tt0000001|          5.7|    1926|
|tt0000002|          5.8|     261|
|tt0000003|          6.5|    1743|
|tt0000004|          5.6|     176|
|tt0000005|          6.2|    2555|
|tt0000006|          5.1|     175|
|tt0000007|          5.4|     797|
|tt0000008|          5.4|    2070|
|tt0000009|          5.3|     200|
|tt0000010|          6.9|    6997|
|tt0000011|          5.3|     357|
|tt0000012|          7.4|   12003|
|tt0000013|          5.7|    1851|
|tt0000014|          7.1|    5383|
|tt0000015|          6.2|    1035|
|tt0000016|          5.9|    1460|
|tt0000017|          4.6|     318|
|tt0000018|          5.3|     583|
|tt0000019|          5.1|      31|
|tt0000020|          4.8|     352|
+---------+-------------+--------+
only showing top 20 rows

0.5449650287628174


In [39]:
#Die Spalte tconst umbenennen, da die spalte in beiden datein gleich heißt
import pyspark.sql.functions as F
ratings_rename=ratings.withColumnRenamed("tconst","rating_id")
ratings_rename.show()

+---------+-------------+--------+
|rating_id|averageRating|numVotes|
+---------+-------------+--------+
|tt0000001|          5.7|    1926|
|tt0000002|          5.8|     261|
|tt0000003|          6.5|    1743|
|tt0000004|          5.6|     176|
|tt0000005|          6.2|    2555|
|tt0000006|          5.1|     175|
|tt0000007|          5.4|     797|
|tt0000008|          5.4|    2070|
|tt0000009|          5.3|     200|
|tt0000010|          6.9|    6997|
|tt0000011|          5.3|     357|
|tt0000012|          7.4|   12003|
|tt0000013|          5.7|    1851|
|tt0000014|          7.1|    5383|
|tt0000015|          6.2|    1035|
|tt0000016|          5.9|    1460|
|tt0000017|          4.6|     318|
|tt0000018|          5.3|     583|
|tt0000019|          5.1|      31|
|tt0000020|          4.8|     352|
+---------+-------------+--------+
only showing top 20 rows



In [40]:
#Spark zwei Dateien mergen
#Datei wird als alias gespeichert um diese besser zu initialisieren
# Für Join erste und zweite Datei machen 
ta = basics.alias('ta')
tb = ratings_rename.alias('tb') 

# Join zwei Dokumente miteinander, how= kann -> 'full' , 'right' , 'left' oder 'innerjoin' sein
# Joinen immer auf die Spalte, welche die gleichen ID's haben
Datei_join = ta.join(tb, ta.tconst == tb.rating_id, how='full')
# Datei mal ausgeben
Datei_join.show()

+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+---------+-------------+--------+
|   tconst|titleType|        primaryTitle|       originalTitle|isAdult|startYear|endYear|runtimeMinutes|           genres|rating_id|averageRating|numVotes|
+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+---------+-------------+--------+
|tt0000008|    short|Edison Kinetoscop...|Edison Kinetoscop...|      0|     1894|     \N|             1|Documentary,Short|tt0000008|          5.4|    2070|
|tt0000015|    short| Autour d'une cabine| Autour d'une cabine|      0|     1894|     \N|             2|  Animation,Short|tt0000015|          6.2|    1035|
|tt0000019|    short|    The Clown Barber|    The Clown Barber|      0|     1898|     \N|            \N|     Comedy,Short|tt0000019|          5.1|      31|
|tt0000051|    short|The Bohemian Enca...|Campement de bohé...| 

In [41]:
#Entfernen von rating_id da sie sonst doppelt sind
daten_drop=Datei_join.drop("rating_id")
daten_drop.show()

+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+-------------+--------+
|   tconst|titleType|        primaryTitle|       originalTitle|isAdult|startYear|endYear|runtimeMinutes|           genres|averageRating|numVotes|
+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+-------------+--------+
|tt0000008|    short|Edison Kinetoscop...|Edison Kinetoscop...|      0|     1894|     \N|             1|Documentary,Short|          5.4|    2070|
|tt0000015|    short| Autour d'une cabine| Autour d'une cabine|      0|     1894|     \N|             2|  Animation,Short|          6.2|    1035|
|tt0000019|    short|    The Clown Barber|    The Clown Barber|      0|     1898|     \N|            \N|     Comedy,Short|          5.1|      31|
|tt0000051|    short|The Bohemian Enca...|Campement de bohé...|      0|     1896|     \N|            \N|Documentary,Short|  

In [42]:
#Alle \N Einträge löschen
data_remove=daten_drop.replace("\\N","")
data_remove.show()

+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+-------------+--------+
|   tconst|titleType|        primaryTitle|       originalTitle|isAdult|startYear|endYear|runtimeMinutes|           genres|averageRating|numVotes|
+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+-------------+--------+
|tt0000008|    short|Edison Kinetoscop...|Edison Kinetoscop...|      0|     1894|       |             1|Documentary,Short|          5.4|    2070|
|tt0000015|    short| Autour d'une cabine| Autour d'une cabine|      0|     1894|       |             2|  Animation,Short|          6.2|    1035|
|tt0000019|    short|    The Clown Barber|    The Clown Barber|      0|     1898|       |              |     Comedy,Short|          5.1|      31|
|tt0000051|    short|The Bohemian Enca...|Campement de bohé...|      0|     1896|       |              |Documentary,Short|  

In [44]:
data_remove.printSchema()

root
 |-- tconst: string (nullable = true)
 |-- titleType: string (nullable = true)
 |-- primaryTitle: string (nullable = true)
 |-- originalTitle: string (nullable = true)
 |-- isAdult: string (nullable = true)
 |-- startYear: string (nullable = true)
 |-- endYear: string (nullable = true)
 |-- runtimeMinutes: string (nullable = true)
 |-- genres: string (nullable = true)
 |-- averageRating: string (nullable = true)
 |-- numVotes: string (nullable = true)



In [45]:
#Da alle Daten Strings sind, umwandeln des Datentypes
import pyspark.sql.types as T
dataframe =(
    data_remove.withColumn("startYear",F.col("startYear").cast(T.IntegerType())).withColumn("endYear",F.col("endYear").cast(T.IntegerType()))
    .withColumn("averageRating",F.col("averageRating").cast(T.FloatType()))
    .withColumn("numVotes",F.col("numVotes").cast(T.IntegerType()))
    .withColumn("isAdult",F.col("isAdult").cast(T.IntegerType()))
    .withColumn("runtimeMinutes",F.col("runtimeMinutes").cast(T.FloatType()))
    
)
dataframe.show()
dataframe.printSchema()
    

+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+-------------+--------+
|   tconst|titleType|        primaryTitle|       originalTitle|isAdult|startYear|endYear|runtimeMinutes|           genres|averageRating|numVotes|
+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+-------------+--------+
|tt0000008|    short|Edison Kinetoscop...|Edison Kinetoscop...|      0|     1894|   null|           1.0|Documentary,Short|          5.4|    2070|
|tt0000015|    short| Autour d'une cabine| Autour d'une cabine|      0|     1894|   null|           2.0|  Animation,Short|          6.2|    1035|
|tt0000019|    short|    The Clown Barber|    The Clown Barber|      0|     1898|   null|          null|     Comedy,Short|          5.1|      31|
|tt0000051|    short|The Bohemian Enca...|Campement de bohé...|      0|     1896|   null|          null|Documentary,Short|  

In [46]:
#Erstetzen der null werte durch 0
data_remove_null=dataframe.na.fill(0)
data_remove_null.show()

+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+-------------+--------+
|   tconst|titleType|        primaryTitle|       originalTitle|isAdult|startYear|endYear|runtimeMinutes|           genres|averageRating|numVotes|
+---------+---------+--------------------+--------------------+-------+---------+-------+--------------+-----------------+-------------+--------+
|tt0000008|    short|Edison Kinetoscop...|Edison Kinetoscop...|      0|     1894|      0|           1.0|Documentary,Short|          5.4|    2070|
|tt0000015|    short| Autour d'une cabine| Autour d'une cabine|      0|     1894|      0|           2.0|  Animation,Short|          6.2|    1035|
|tt0000019|    short|    The Clown Barber|    The Clown Barber|      0|     1898|      0|           0.0|     Comedy,Short|          5.1|      31|
|tt0000051|    short|The Bohemian Enca...|Campement de bohé...|      0|     1896|      0|           0.0|Documentary,Short|  

In [48]:
Movie_Daten=data_remove_null.coalesce(1).write.option("header","true").csv("Spark/MovieDaten2.csv")

In [ ]:
from pymongo import MongoClient
import csv
#so würde es eigentlich gehen, aber vm ist kacke und stürzt ab
# specify the MongoDB server host and port
host = "localhost"
port = 27017

# create a MongoClient instance
client = MongoClient(host, port)

# specify the database and collection names
db_name = "Movie_Daten"
collection_name = "MovieDaten"

# get a reference to the database and collection
db = client[db_name]
collection = db[collection_name]

# open the CSV file and read the data
with open("Desktop/Spark/MovieDaten.csv/part-00000-a5f97438-95d8-483b-bc98-31b2c2ca1f3b-c000.csv") as csv_file:
    reader = csv.DictReader(csv_file)
    data = list(reader)

# insert the data into the collection
result = collection.insert_many(data)

In [15]:
#Verbindung zur DB herstellen da die Daten über den compass hochgeladen wurden
from pymongo import MongoClient
import csv
#so würde es eigentlich gehen, aber vm ist kacke und stürzt ab
# specify the MongoDB server host and port
host = "localhost"
port = 27017

# create a MongoClient instance
client = MongoClient(host, port)

# specify the database and collection names
db_name = "Movie_Daten"
collection_name = "Movie"

# get a reference to the database and collection
db = client[db_name]
collection = db[collection_name]



# Aggregations auf die DB

In [23]:
#Finde alle Filme ab dem Jahr 2013

movie_time=(
    [
        {
            "$match":{"startYear":{"$gte":2013}}
        },

        {
            "$project":{"primaryTitle":1,"startYear":1}
            
        },
        {
            "$sort":{"startYear":-1}
        }
    
        
        
        
    ]
    
)
pprint.pprint(list(collection.aggregate(movie_time)))
        


[{'_id': ObjectId('63a1c5d676e921d91fbf50de'),
  'primaryTitle': 'Loose Translation',
  'startYear': 2029},
 {'_id': ObjectId('63a1c5cf76e921d91fbcb63d'),
  'primaryTitle': "The Adventures of Tintin: Red Rackham's Treasure",
  'startYear': 2027},
 {'_id': ObjectId('63a1c5d276e921d91fbda038'),
  'primaryTitle': 'The competition',
  'startYear': 2027},
 {'_id': ObjectId('63a1c5d376e921d91fbdec59'),
  'primaryTitle': 'Monopoly',
  'startYear': 2027},
 {'_id': ObjectId('63a1c5d176e921d91fbd2ab2'),
  'primaryTitle': 'Walking In Darkness II',
  'startYear': 2025},
 {'_id': ObjectId('63a1c5d176e921d91fbd1e03'),
  'primaryTitle': 'The Advocate',
  'startYear': 2024},
 {'_id': ObjectId('63a1c5d176e921d91fbd5577'),
  'primaryTitle': 'Kaithi 2',
  'startYear': 2024},
 {'_id': ObjectId('63a1c5d276e921d91fbdbd04'),
  'primaryTitle': 'Episode #1.4',
  'startYear': 2024},
 {'_id': ObjectId('63a1c5d376e921d91fbde9fd'),
  'primaryTitle': 'Furiosa',
  'startYear': 2024},
 {'_id': ObjectId('63a1c5d376e92

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



,
  'startYear': 2017},
 {'_id': ObjectId('63a1c5d376e921d91fbde8f9'),
  'primaryTitle': 'Sutton United',
  'startYear': 2017},
 {'_id': ObjectId('63a1c5d376e921d91fbde8fa'),
  'primaryTitle': 'Cruising the Internet',
  'startYear': 2017},
 {'_id': ObjectId('63a1c5d376e921d91fbde8fd'),
  'primaryTitle': 'Pepper Behind the Scenes!',
  'startYear': 2017},
 {'_id': ObjectId('63a1c5d376e921d91fbde91b'),
  'primaryTitle': "JFK Jr.'s Tragic Final Flight (Part 1)",
  'startYear': 2017},
 {'_id': ObjectId('63a1c5d376e921d91fbde9ea'),
  'primaryTitle': 'Axia Home Loans',
  'startYear': 2017},
 {'_id': ObjectId('63a1c5d376e921d91fbdea05'),
  'primaryTitle': 'El último regalo',
  'startYear': 2017},
 {'_id': ObjectId('63a1c5d376e921d91fbdea20'),
  'primaryTitle': 'The Fascinating Dream',
  'startYear': 2017},
 {'_id': ObjectId('63a1c5d376e921d91fbdea25'),
  'primaryTitle': 'Wo Gorgeous Teens Making out On the Beach',
  'startYear': 2017},
 {'_id': ObjectId('63a1c5d376e921d91fbdea35'),
  'primaryT

In [33]:
#Finde alle Filme die Short sind und zähle diese
movie_type=([
    {
        "$match":{"titleType":{"$regex":"^short"}}
    },
    {
        "$project":{"titleType":1,"primaryTitle":1}
    },
    {
        "$count":"titleType"
    }
    


])
pprint.pprint(list(collection.aggregate(movie_type)))

[{'titleType': 28140}]
